In [37]:
import pandas as pd

In [38]:
# Overall data
train_data = pd.read_pickle(open("tweets-data/train.pkl", "rb"))
dev_data = pd.read_pickle(open("tweets-data/dev.pkl", "rb"))

pd.set_option('display.max_colwidth', None)
train_data

text  \
0                                           _TWITTER-ENTITY_ i go at 4 lol   
1           _TWITTER-ENTITY_ I let it all out last night . I need you here   
2                                                 _TWITTER-ENTITY_ so do I   
3                                  Girl on the mans I love yo body . #Loui   
4       _TWITTER-ENTITY_ yu made me spit on this boy just now iam in tears   
...                                                                    ...   
39995                                     _TWITTER-ENTITY_ tell me bout it   
39996  â _TWITTER-ENTITY_ : Really hate girls with individuals âï¸â   
39997       Oomf Taking To Long To Text Back ! I'm Fina Turn Up On His Ass   
39998                                                 Jk . Not happening .   
39999                                     Lil Snupe Still Heavy On My Mind   

      Sentiment Demographic  
0      negative         AAE  
1      negative         AAE  
2      positive         SAE  
3      positive         AAE  
4      positive         AAE  
...         ...         ...  
39995  positive         SAE  
39996  negative         AAE  
39997  negative         AAE  
39998  positive         SAE  
39999  negative         AAE  

[40000 rows x 3 columns]

### Original Text

In [39]:
for row in range(len(train_data)):
    print(train_data.loc[row, 'text'])

_TWITTER-ENTITY_ i go at 4 lol
_TWITTER-ENTITY_ I let it all out last night . I need you here
_TWITTER-ENTITY_ so do I
Girl on the mans I love yo body . #Loui
_TWITTER-ENTITY_ yu made me spit on this boy just now iam in tears
That outfit is horrible
I think I wana go to the Fright Fest
_TWITTER-ENTITY_ happy thanksgiving
When your room smells like weed for the third day in a row #gross
â _TWITTER-ENTITY_ : Niggas hate being in the friend zone â damn right
Going To Get My Ears Pierced Later On Today
Been best friends for 2 years and don't have a single picture together
I are so unhealthy last night
_TWITTER-ENTITY_ NICE AZZ
Yep . I'm going to sleep as soon as I get to Brandon's tomorrow .
_TWITTER-ENTITY_ yeah cuz i totally needed to be reminded of that
Trying to bool with oomf tomorro , Kant go ta school anyway â
I thought you were better than that . You were so sweet and fun to hang with .
I'm ready to decorate
Currently fw oomf
_TWITTER-ENTITY_ need to be with that nasty mouth


### Reduce noise

In [40]:
for row in range(len(train_data)):
    original = train_data.loc[row, 'text']
    new = original.replace('_TWITTER-ENTITY_ ', '')
    new = new.replace('_TWITTER-ENTITY_', '')
    if new[0] == '\\':
        new = new.replace('\\', '', 1)
    new = new.strip()
    print(new)

i go at 4 lol
I let it all out last night . I need you here
so do I
Girl on the mans I love yo body . #Loui
yu made me spit on this boy just now iam in tears
That outfit is horrible
I think I wana go to the Fright Fest
happy thanksgiving
When your room smells like weed for the third day in a row #gross
â : Niggas hate being in the friend zone â damn right
Going To Get My Ears Pierced Later On Today
Been best friends for 2 years and don't have a single picture together
I are so unhealthy last night
NICE AZZ
Yep . I'm going to sleep as soon as I get to Brandon's tomorrow .
yeah cuz i totally needed to be reminded of that
Trying to bool with oomf tomorro , Kant go ta school anyway â
I thought you were better than that . You were so sweet and fun to hang with .
I'm ready to decorate
Currently fw oomf
need to be with that nasty mouth
Can't wait to see Levi tackle some munchkins tonight
IMMA BE COOL
When you find out who really appreciates your presence , it's the best feeling in the w

In [41]:
def remove_noise(original):
    new = original.replace('_TWITTER-ENTITY_ ', '')
    new = new.replace('_TWITTER-ENTITY_', '')
    if new[0] == '\\':
        new = new.replace('\\', '', 1)
    new = new.strip()
    return new

In [42]:
# Remove noise for train data
for row in range(len(train_data)):
    train_data.loc[row, 'text'] = remove_noise(train_data.loc[row, 'text'])

train_data

text  \
0                                                       i go at 4 lol   
1                       I let it all out last night . I need you here   
2                                                             so do I   
3                             Girl on the mans I love yo body . #Loui   
4                   yu made me spit on this boy just now iam in tears   
...                                                               ...   
39995                                                 tell me bout it   
39996              â : Really hate girls with individuals âï¸â   
39997  Oomf Taking To Long To Text Back ! I'm Fina Turn Up On His Ass   
39998                                            Jk . Not happening .   
39999                                Lil Snupe Still Heavy On My Mind   

      Sentiment Demographic  
0      negative         AAE  
1      negative         AAE  
2      positive         SAE  
3      positive         AAE  
4      positive         AAE  
...         ...         ...  
39995  positive         SAE  
39996  negative         AAE  
39997  negative         AAE  
39998  positive         SAE  
39999  negative         AAE  

[40000 rows x 3 columns]

In [43]:
# Remove noise for dev data
for row in range(len(dev_data)):
    dev_data.loc[row, 'text'] = remove_noise(dev_data.loc[row, 'text'])

dev_data

text  \
0                                                We moving !! But not far nbs . I wanted to move back west but wateva   
1                                                                                               White baby for sale !   
2                                                                                                Just had to call 911   
3                                                                            this lonely shit is true SIKE NIGGAAAAAA   
4                                                                                          Bestest nigga get it right   
...                                                                                                               ...   
3995                                                                                        Steven A . is going off .   
3996                                                                            Sierra was throwing it back lastnight   
3997                                                 oh I understand I just thought it was funny that you tagged them   
3998                          Y'all remember when mf's use to say \lil daddy ? " Straight THROWBACK ! #sikestonshit "   
3999  â : Listening to August I luv it imma give #1omf a lap dance to dis cuz man I luv this shit âthat's my shit   

     Sentiment Demographic  
0     negative         AAE  
1     positive         SAE  
2     negative         SAE  
3     negative         AAE  
4     positive         AAE  
...        ...         ...  
3995  positive         SAE  
3996  positive         AAE  
3997  positive         SAE  
3998  positive         AAE  
3999  negative         AAE  

[4000 rows x 3 columns]

### Regenerate Text Embeddings

In [44]:
def generate_embedding(model, data):
    sentences = data['text']
    sentence_embeddings = model.encode(sentences)

    data['TFIDF'] = list(sentence_embeddings)
    return data

In [45]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-MiniLM-L6-v2')

clean_train_data = generate_embedding(model, train_data)
clean_dev_data = generate_embedding(model, dev_data)
clean_dev_data

text  \
0                                                We moving !! But not far nbs . I wanted to move back west but wateva   
1                                                                                               White baby for sale !   
2                                                                                                Just had to call 911   
3                                                                            this lonely shit is true SIKE NIGGAAAAAA   
4                                                                                          Bestest nigga get it right   
...                                                                                                               ...   
3995                                                                                        Steven A . is going off .   
3996                                                                            Sierra was throwing it back lastnight   
3997                                                 oh I understand I just thought it was funny that you tagged them   
3998                          Y'all remember when mf's use to say \lil daddy ? " Straight THROWBACK ! #sikestonshit "   
3999  â : Listening to August I luv it imma give #1omf a lap dance to dis cuz man I luv this shit âthat's my shit   

     Sentiment Demographic  \
0     negative         AAE   
1     positive         SAE   
2     negative         SAE   
3     negative         AAE   
4     positive         AAE   
...        ...         ...   
3995  positive         SAE   
3996  positive         AAE   
3997  positive         SAE   
3998  positive         AAE   
3999  negative         AAE   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             TFIDF  
0                                 [0.08153297, -0.057129562, 0.03301466, -0.04007373, 0.036982812, -0.0009929638, -0.04419778, -0.044694126, -0.03624601, -0.005134629, -0.06383605, -0.037742294, 0.028927222, -0.029653316, -0.01036672, -0.015982235, 0.008944151, -0.0911021, -0.025041, -0.0052783643, -0.058242265, 0.019823382, -0.045503728, 0.019796053, 0.06813926, 0.07565475, 0.023764243, 0.041146122, 0.012114321, -0.06541791, 0.03971105, -0.007356014, -0.030228477, -0.0360277, 0.08500528, 0.026702767, 0.025974045, -0.06145622, 0.024791535, -0.031224865, 0.048847783, 0.066743694, 0.03604564, 0.09060225, -0.037762534, 0.065781586, -0.018407995, 0.011795298, 0.09686386, 0.06365306, 0.039593615, 0.012893218, -0.1015751, 0.047737435, 0.0071573644, 0.1722083, 0.019955818, -0.027497038, 0.0060352953, -0.032669112, 0.022604583, 0.08569951, 0.06736823, 0.022519821, -0.015698425, -0.009678554, -0.051950194, 0.02794362, 0.011039954, -0.10249951, -

In [46]:
# Store dataframe with new embedding as file
clean_train_data.to_pickle('sentence-transformers/clean_train_emb.pkl')
clean_dev_data.to_pickle('sentence-transformers/clean_dev_emb.pkl')